In [1]:
# created on Dec 24, 2020
# @author:          Bo Zhao
# @email:           zhaobo@uw.edu
# @website:         https://hgis.uw.edu
# @organization:    Department of Geography, University of Washington, Seattle
# @description:     Search geo-tagged tweets within the U.S. This script is modified from https://github.com/shawn-terryah/Twitter_Geolocation

!python -m pip install tweepy
import tweepy, json, time

In [2]:
class StreamListener(tweepy.StreamListener):
    """tweepy.StreamListener is a class provided by tweepy used to access
    the Twitter Streaming API to collect tweets in real-time.
    """

    def __init__(self, time_limit=60, file=""):
        """class initialization"""
        self.start_time = time.time()
        self.limit = time_limit
        self.f = open(file, 'a', encoding="utf-8")
        super(StreamListener, self).__init__()

    def on_data(self, data):
        """This is called when data are streamed in."""
        if (time.time() - self.start_time) < self.limit:
            datajson = json.loads(data)
            print(datajson, "\n")
            if 'id' not in datajson.keys():
                time.sleep(10)
            else:
                # {'limit': {'track': 13, 'timestamp_ms': '1585851016736'}}

                id = datajson['id']
                username = datajson['user']['screen_name']
                created_at = datajson['created_at']
                text = datajson['text'].strip().replace("\n", "")

                # process the geo-tags
                if datajson['coordinates'] == None:
                    try:
                        bbox = datajson['place']['bounding_box']['coordinates'][0]
                        lng = (bbox[0][0] + bbox[2][0]) / 2.0
                        lat = (bbox[0][1] + bbox[1][1]) / 2.0
                    except:
                        lat = 0
                        lng = 0
                else:
                    lng = datajson['coordinates']['coordinates'][0]
                    lat = datajson['coordinates']['coordinates'][1]

                if lat != 0:
                    record = '%s, %s, %f, %f, %s \n' % (username, created_at, lng, lat, text)
                    print(record)
                    self.f.write(record)
                else:
                    pass
        else:
            self.f.close()
            print("finished")
            return False

In [6]:
if __name__ == "__main__":
    # These are provided to you through the Twitter API after you create a account
    # register a Twitter App to get the keys and access tokens.
    output_file = "assets/tweets.csv"

    # Apply for your own Twitter API keys at https://developer.twitter.com/en/apply-for-access
    consumer_key = "DACx67WmFCpTOUQAfrFJmp17i"
    consumer_secret = "x4emq3PWq6VRNNjFACDWMoBRntI79F5pFbgOP37S3Xi7j6kTbM"
    access_token = "893926026-01AAWI0vFAg4erwZjWc1tvojACyblqgjjDiaSUDJ"
    access_token_secret = "YwO1eJa2vBvRlvg9PVrmOcxCsJjv3E2V8XHxsSUaCpxKm"

    myauth = tweepy.OAuthHandler(consumer_key, consumer_secret)
    myauth.set_access_token(access_token, access_token_secret)

    # LOCATIONS are the longitude, latitude coordinate corners for a box that restricts the
    # geographic area from which you will stream tweets. The first two define the southwest
    # corner of the box and the second two define the northeast corner of the box.
    LOCATIONS = [-124.7771694, 24.520833, -66.947028, 49.384472,  # Contiguous US
                 -164.639405, 58.806859, -144.152365, 71.76871,  # Alaska
                 -160.161542, 18.776344, -154.641396, 22.878623]  # Hawaii

    stream_listener = StreamListener(time_limit=14400, file=output_file)
    stream = tweepy.Stream(auth=myauth, listener=stream_listener)
    stream.filter(track=['#wallstreetbets'], is_async=True)
    #stream.filter(locations=LOCATIONS)

{'created_at': 'Sat Jan 30 02:56:15 +0000 2021', 'id': 1355349075915231238, 'id_str': '1355349075915231238', 'text': 'RT @SecureProfit: Got these suits mad, live footage from the offices of @CitronResearch &amp; Melvin Capital 😂😂😂 #FreeWallStreetBets #wallstree…', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1327237039201210370, 'id_str': '1327237039201210370', 'name': 'ldwest', 'screen_name': 'ldwest2', 'location': None, 'url': None, 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 24, 'friends_count': 199, 'listed_count': 0, 'favourites_count': 17427, 'statuses_count': 2205, 'created_at': 'Fri Nov 13 13:09:19 +0000 2020', 'utc_offset': None, 'time_zone': None, 'geo_enabled': False, 'la

{'created_at': 'Sat Jan 30 02:56:15 +0000 2021', 'id': 1355349077513265158, 'id_str': '1355349077513265158', 'text': "RT @cryptomasterjam: I'll give 30$ in 12hrs that retweets and tweet the following text with picture 👇\n\nA large discord that is partnered wi…", 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1318849847701630976, 'id_str': '1318849847701630976', 'name': 'rylee', 'screen_name': 'luckyriririkiim', 'location': None, 'url': None, 'description': 'i will win🤞☘️ || back up @/riririkiiim', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 267, 'friends_count': 3013, 'listed_count': 0, 'favourites_count': 11135, 'statuses_count': 15502, 'created_at': 'Wed Oct 21 09:41:54 +0000 2020', 'utc_offset': None

{'created_at': 'Sat Jan 30 02:56:19 +0000 2021', 'id': 1355349090972954624, 'id_str': '1355349090972954624', 'text': "RT @cashdaddiespod: New #CashDaddies podcast is out tomorrow 1/29! We're talking #wallstreetbets , #Crypto and big picks for the next week.…", 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 3354365434, 'id_str': '3354365434', 'name': 'Howie Dewey', 'screen_name': 'howie_dewey', 'location': 'NYC', 'url': 'https://www.youtube.com/channel/UClDSPn1XXi6Icm4Te6vjzOg', 'description': 'Father, Comedian, Actor 📍NYC, ATL, LA', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 117, 'friends_count': 94, 'listed_count': 3, 'favourites_count': 680, 'statuses_count': 454, 'created_at': 'Thu Jul 02 02:21:25 +00

{'created_at': 'Sat Jan 30 02:56:26 +0000 2021', 'id': 1355349121842860035, 'id_str': '1355349121842860035', 'text': 'RT @amircrypto: @CaitlinLong_ @Bitcoin https://t.co/w3qdEF011e', 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1354091092061245440, 'id_str': '1354091092061245440', 'name': 'Giovanni Montano', 'screen_name': 'Giovann49677103', 'location': None, 'url': None, 'description': 'I am not a vegan', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 0, 'friends_count': 2, 'listed_count': 0, 'favourites_count': 6, 'statuses_count': 24, 'created_at': 'Tue Jan 26 15:37:34 +0000 2021', 'utc_offset': None, 'time_zone': None, 'geo_enabled': False, 'lang': None, 'contributors_enabled': False, 'is_translator': False, 'pro

{'created_at': 'Sat Jan 30 02:56:27 +0000 2021', 'id': 1355349126930702338, 'id_str': '1355349126930702338', 'text': 'Stop watching the green line go up and brush your teeth!', 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1351679015631859716, 'id_str': '1351679015631859716', 'name': 'Burlap & Flax.', 'screen_name': 'BurlapAndFlax', 'location': None, 'url': None, 'description': 'Curating a simpler life @\nhttps://burlapandflax.wordpress.com', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 2, 'friends_count': 48, 'listed_count': 0, 'favourites_count': 38, 'statuses_count': 64, 'created_at': 'Tue Jan 19 23:53:00 +0000 2021', 'utc_offset': None, 'time_zone': None, 'geo_enabled': False, 'lang': None, 'contributors_enabled

...

{'created_at': 'Sat Jan 30 03:40:01 +0000 2021', 'id': 1355360089952149505, 'id_str': '1355360089952149505', 'text': 'RT @justinsuntron: #wallstreetbets whale: SPREAD THE NEWS, $TRX —&gt; 🌘 #TRON https://t.co/ulxrKrsMj8', 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1419757483, 'id_str': '1419757483', 'name': '\u200f فهده', 'screen_name': 'parodispor', 'location': 'ksa', 'url': None, 'description': '﴿ ﺣـٰﺂﺄﯛلت ﺂﺄڪﯛن ﭑاﻧﺳﭑنهۃ ﻟڪـٰن ﭑﻟﺳڪر ﺳڪـٰر', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 13, 'friends_count': 65, 'listed_count': 0, 'favourites_count': 9, 'statuses_count': 20, 'created_at': 'Sat May 11 04:19:42 +0000 2013', 'utc_offset': None, 'time_zone': None, 'geo_enabled': False, 'lang': None, 'contributors_enab

{'created_at': 'Sat Jan 30 03:40:04 +0000 2021', 'id': 1355360104040849409, 'id_str': '1355360104040849409', 'text': 'RT @justinsuntron: #wallstreetbets whale: SPREAD THE NEWS, $TRX —&gt; 🌘 #TRON https://t.co/ulxrKrsMj8', 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1173073639, 'id_str': '1173073639', 'name': '\u200fآزال .', 'screen_name': 'esra_ozbas1', 'location': 'ksa', 'url': None, 'description': 'شيئاً مـِآِآِ بدِآخلي .. يُشعِرُني وڳٌأنني ملڳ', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 0, 'friends_count': 24, 'listed_count': 0, 'favourites_count': 8, 'statuses_count': 15, 'created_at': 'Tue Feb 12 20:57:28 +0000 2013', 'utc_offset': None, 'time_zone': None, 'geo_enabled': False, 'lang': None, 'contributors_

{'created_at': 'Sat Jan 30 03:40:05 +0000 2021', 'id': 1355360107979288579, 'id_str': '1355360107979288579', 'text': 'RT @ArcadiaEconomic: Breaking #Silver News: $SLV added 37 mil ozs on Friday! (according to their data)\n\nhttps://t.co/cmnciZxd8Q \n\n@profitsp…', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1314383712524566528, 'id_str': '1314383712524566528', 'name': 'Hindu Hustler “SQUEEZE THE SILVER SHORTS”', 'screen_name': 'HustlerHindu', 'location': None, 'url': None, 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 50, 'friends_count': 32, 'listed_count': 0, 'favourites_count': 626, 'statuses_count': 1739, 'created_at': 'Fri Oct 09 01:54:48 +0000 2020', 'utc_offset': None, 'time_z

{'created_at': 'Sat Jan 30 03:40:07 +0000 2021', 'id': 1355360116388868096, 'id_str': '1355360116388868096', 'text': 'RT @justinsuntron: #wallstreetbets whale: SPREAD THE NEWS, $TRX —&gt; 🌘 #TRON https://t.co/ulxrKrsMj8', 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 902304974461444097, 'id_str': '902304974461444097', 'name': '\u200f رسيل', 'screen_name': 'hrykngr', 'location': 'ksa', 'url': None, 'description': 'الله اكبر', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 6, 'friends_count': 75, 'listed_count': 0, 'favourites_count': 7, 'statuses_count': 16, 'created_at': 'Mon Aug 28 23:00:44 +0000 2017', 'utc_offset': None, 'time_zone': None, 'geo_enabled': False, 'lang': None, 'contributors_enabled': False, 'is_trans

{'created_at': 'Sat Jan 30 03:40:10 +0000 2021', 'id': 1355360127730257921, 'id_str': '1355360127730257921', 'text': '#dogecoin during the dip\n\n#WALLSTREETBETS #ROBINHOOD #CRYPTO #GME #NKD #WSB #BB #NOK #AMC #STOCKS #INVESTING… https://t.co/6jM8mmAY0g', 'display_text_range': [0, 140], 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'truncated': True, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1098778855685455908, 'id_str': '1098778855685455908', 'name': 'Drew Do’sit', 'screen_name': 'drewdosit', 'location': 'Lakeville, MN', 'url': None, 'description': 'Sports, Lakes and Family.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 2, 'friends_count': 8, 'listed_count': 0, 'favourites_count': 57, 'statuses_count': 42, 'created_at': 'Fri Feb 22 02:57:48 +0000 2019', 'utc_offset': None, 